In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/check-it-out/legal_cases_with_docs_new.csv
/kaggle/input/legalsummary/HFsummarydataset.csv
/kaggle/input/legal-text-classification-dataset/legal_text_classification.csv


In [2]:
!pip install llama-index pinecone sentence-transformers
!pip install llama-index-vector-stores-pinecone
!pip install groq rouge-score

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 421.9/421.9 kB 15.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 45.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 50.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 253.1/253.1 kB 15.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 644.8/644.8 kB 26.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.2/129.2 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: platformdirs
    Found existing installation: platformdirs 4.3.6
    Uninstalling platformdirs-4.3.6:
      Successfully uninstalled platformdirs-4.3.6
  Attempting uninstall: nltk
    Found existing installation: nltk 3.2.4
    Uninstalling nltk-3.2.4:
      Successfully uninstalled nltk-3.2.4
  Attempting uninstall: openai
    Found existing installation: openai 1.57.4
    Uninstalling openai-1.57.4:
      Successfu

In [3]:
from pinecone import Pinecone, ServerlessSpec
from llama_index.core import (
    VectorStoreIndex,
    StorageContext,
    SimpleDirectoryReader,
)
from llama_index.vector_stores.pinecone import PineconeVectorStore

# Initialize Pinecone
pc = Pinecone(api_key="pcsk_7E1vP3_QK2W6M9XCiHufegYYXyYurwWGddethJCY4TYTcm15PnRKS5EDMKa11KyYvNjVbB")
pc_duplicate = Pinecone(api_key="pcsk_7VMsMN_PRA9cnkzr5tpG92dfxqxcAhhczX6RwifiDqkCTa4ruyWZX5AXyJNgiCezztAgvT")
query_pc = Pinecone(api_key="pcsk_6zNLd7_Lep8rBqzNatyGXGykxBumtiAcYE493jHtrgTkjhuJYdDBGeByH8KXAFYVdXLjrq")

# Create a Pinecone index
index_name = "legaltextcasesummary"
if index_name not in pc.list_indexes().names():
    pc.create_index(
        name=index_name, 
        dimension=1024, 
        metric='cosine',
        spec=ServerlessSpec(
            cloud='aws',
            region='us-east-1'
        )
    )




In [4]:
time_duration_upsert = []
time_duration_rag = []
num_chunks = []

# Q/A dataset

In [5]:

from groq import Groq

import random

import time
import re

# Set up Groq client
groq_client = Groq(api_key="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")

def isSimilarQuery(query):
    try:
        q_index_name = "legaltextcasequery"

        if q_index_name not in query_pc.list_indexes().names():
            pc_duplicate.create_index(
                name=q_index_name,
                dimension=1024,
                metric='cosine',
                spec=ServerlessSpec(
                    cloud='aws',
                    region='us-east-1'
                )
            )

        query_embedding = pc_duplicate.inference.embed(
            model="multilingual-e5-large",
            inputs=[query],
            parameters={
                "input_type": "query"
            }
        )

        query_vector = query_embedding[0].values

        # Check if the query was already asked before
        q_results = query_pc.Index(q_index_name).query(
            namespace="q_ind",
            vector=query_vector,
            top_k=3,
            include_values=False,
            include_metadata=True 
        )

        if q_results['matches'] and q_results['matches'][0]['score'] >= 0.8:
            print('Query Present in q_ind')
            return q_results['matches'][0]['metadata']['text']

        # If not found, search all legal document namespaces
        best_match = None
        best_score = -1.0
        best_namespace = None

        legal_index = pc.Index(index_name)

        top_k = 3
        for i in range(1, 42):
            namespace = f"ind_{i}"
            try:
                results = legal_index.query(
                    namespace=namespace,
                    vector=query_vector,
                    top_k=top_k,
                    include_values=False,
                    include_metadata=True
                )

                for match in results['matches']:
                    if match and match['score'] > best_score:
                        best_score = match['score']
                        best_match = match
                        best_namespace = namespace

            except Exception as ns_err:
                print(f"Error querying namespace {namespace}: {ns_err}")


        if best_match:
            # Add the query to the q_ind namespace for future lookup
            best_match['metadata']['query'] = query
            query_pc.Index(q_index_name).upsert(
                vectors=[{
                    "id": best_match['id'],
                    "values": query_vector,
                    "metadata": best_match['metadata']
                }],
                namespace="q_ind"
            )
            print(f'Query Upserted from {best_namespace} with score {best_score:.3f}')
            return best_match['metadata']['text']

        return "No relevant information found in any namespace."

    except Exception as e:
        print(f"Error in isSimilarQuery: {e}")
        raise HTTPException(status_code=500, detail="Error processing query")

def generate_answer(query, retrieved_contexts):
    # Extract the text content from retrieved documents
    contexts = []
    retrieved_dict = {}
    # Convert the Pinecone object to a dict for easier handling
    if isinstance(retrieved_contexts, str):
        contexts = [retrieved_contexts]
    elif isinstance(retrieved_contexts, dict):
        retrieved_dict = retrieved_contexts
        if 'matches' in retrieved_dict:
            for match in retrieved_dict['matches']:
                if 'metadata' in match and 'text' in match['metadata']:
                    text = match['metadata']['text']
                    if text:
                        contexts.append(text)
    else:
        try:
            retrieved_dict = retrieved_contexts.to_dict()
            if 'matches' in retrieved_dict:
                for match in retrieved_dict['matches']:
                    if 'metadata' in match and 'text' in match['metadata']:
                        text = match['metadata']['text']
                        if text:
                            contexts.append(text)
        except Exception as e:
            print(f"Error extracting context: {e}")

    
    # Extract text from matches
    if 'matches' in retrieved_dict:
        for match in retrieved_dict['matches']:
            if 'metadata' in match and 'text' in match['metadata']:
                # In a real scenario this would contain the actual text
                text = match['metadata']['text']
                if text:  # Only add non-empty text
                    contexts.append(text)
    
    context_text = "\n\n".join(contexts)
    prompt = f"""
You are a helpful assistant specialized in Indian tax law. Use ONLY the following context to answer the question. 
If you don't have enough information to answer this question, say "I don't have enough information to answer this question."

Context:
{context_text}

Question: {query}

Answer:
"""
    
    # Generate answer using Groq's LLama model
    try:
        response = groq_client.chat.completions.create(
            model="llama3-70b-8192",
            messages=[
                {"role": "system", "content": "You are a helpful assistant that answers questions based only on the provided context."},
                {"role": "user", "content": prompt}
            ],
            temperature=0.2,
            max_tokens=1024
        )
        return response.choices[0].message.content
    except Exception as e:
        return f"Error generating response: {str(e)}"

def process_query(query):
    time_duration_upsert.append(0)
    # Add debugging information
    print("Retrieving similar documents...")
    start_time = time.time()
    retrieved_results = isSimilarQuery(query)

    print(f"Type of retrieved_results: {type(retrieved_results)}")
    
    print("Generating answer...")
    answer = generate_answer(query, retrieved_results)
    duration = time.time()-start_time
    time_duration_rag.append(duration)
    return {
        "query": query,
        "retrieved_contexts": retrieved_results,
        "answer": answer
    }

def process_newdata_query(query,document_text):
    start_time = time.time()
    chunks = chunk_text(document_text)
    num_chunks.append(len(chunks))
    namespace,success = upsert_new_chunked_text(chunks)
    duration = time.time()-start_time
    time_duration_upsert.append(duration)
    print(success,' time ',duration)
    if success:
        print("Retrieving similar documents...")
        start_time = time.time()
        retrieved_results = retrieve_when_doc_given(namespace,query)
        print(f"Type of retrieved_results: {type(retrieved_results)}")
        
        print("Generating answer...")
        answer = generate_answer(query, retrieved_results)
        duration = time.time()-start_time
        time_duration_rag.append(duration)
        return {
            "query": query,
            "retrieved_contexts": retrieved_results,
            "answer": answer
        }
    else:
        time_duration_rag.append(0)
        return {
            "query": query,
            "answer":"Failed to upsert documents please try again"
        }

import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download("punkt_tab")  # Download NLTK tokenizer model

def chunk_text(text, max_tokens=505):
    """Splits text into chunks of max 505 tokens while keeping sentence structure intact."""
    sentences = sent_tokenize(text)  # Split into sentences
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        words = word_tokenize(sentence)  # Tokenize words
        sentence_length = len(words)

        if current_length + sentence_length > max_tokens:
            if current_chunk:
                chunks.append(" ".join(current_chunk))  # Save previous chunk
            current_chunk = words  # Start new chunk
            current_length = sentence_length
        else:
            current_chunk.extend(words)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))  # Add last chunk

    return chunks

def upsert_new_chunked_text(chunks):
    data = []
    for j in range(len(chunks)):
        data.append({'id':'ns_'+str(random.randint(75000,1000000))+'_'+str(j),'text':chunks[j],'summary':'NA'})

    for i in range(len(data)):
        namespace_count = 41
        try:
            datas = []
            embeddings = []
            for j in range(1,3):
                # Slice the data batch
                s = i+(j-1)*96
                if s>=len(data):
                    break
                e = min(i+j*96,len(data))
                datas.append(data[s:e])
                # Generate embeddings
                emb = pc_duplicate.inference.embed(
                    model="multilingual-e5-large",
                    inputs=[d['text'] for d in datas[j-1]],
                    parameters={"input_type": "passage", "truncate": "END"}
                )
                embeddings.append(emb) 
                time.sleep(15)

            # Prepare records for Pinecone
            records = []
            for j in range(len(datas)):
                for d, e in zip(datas[j], embeddings[j]):
                    try:
                        # # Truncate text if metadata exceeds the limit
                        truncated_text = d['text']
                        summary_text = d['summary']
                        
                        # Add the record
                        records.append({
                            "id": d['id'],
                            "values": e['values'],
                            "metadata": {"text": truncated_text,'summary':summary_text}
                        })
                    except Exception as inner_error:
                        print(f"Error processing record ID {d['id']}: {inner_error}")
                
            # Upsert records into the Pinecone index
            pinecone_index = pc.Index(index_name)
            pinecone_index.upsert(
                vectors=records,
                namespace=f"ind_{namespace_count}"
            )
            return namespace_count,True
        except Exception as batch_error:
            print(f"Error processing batch {i}: {batch_error}")
            return namespace_count,False

def retrieve_when_doc_given(namespace,query):
    # when a file is uploaded then other type of retrieval
    try:
        query_embedding = pc_duplicate.inference.embed(
            model="multilingual-e5-large",
            inputs=[query],
            parameters={
                "input_type": "query"
            }
        )

        query_vector = query_embedding[0].values

        # If not found, search all legal document namespaces
        best_match = None
        best_score = -1.0
        best_namespace = None

        legal_index = pc.Index(index_name)

        top_k = 3
        try:
            results = legal_index.query(
                namespace=f"ind_{namespace}",
                vector=query_vector,
                top_k=top_k,
                include_values=False,
                include_metadata=True
            )

            for match in results['matches']:
                if match and match['score'] > best_score:
                    best_score = match['score']
                    best_match = match
                    best_namespace = namespace

        except Exception as ns_err:
            print(f"Error querying namespace {namespace}: {ns_err}")


        if best_match:
            # Add the query to the q_ind namespace for future lookup
            best_match['metadata']['query'] = query
            return best_match['metadata']['text']

        return "No relevant information found in any namespace."

    except Exception as e:
        print(f"Error in isSimilarQuery: {e}")
        raise HTTPException(status_code=500, detail="Error processing query")

def clean_text(text: str) -> str:
    # Replace any character that's not a letter, digit, or whitespace with a space.
    cleaned = re.sub(r'[^A-Za-z0-9\s]', ' ', text)
    # Replace one or more whitespace characters with a single space and remove leading/trailing spaces.
    cleaned = re.sub(r'\s+', ' ', cleaned).strip()
    return cleaned

[nltk_data] Downloading package punkt_tab to /usr/share/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [6]:
from rouge_score import rouge_scorer
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from sklearn.metrics import f1_score
from nltk.tokenize import word_tokenize
import pandas as pd
import re
from sentence_transformers import SentenceTransformer
import matplotlib.pyplot as plt
import seaborn as sns

In [7]:
# 1. ROUGE Score with individual plots
def calculate_rouge(predictions, references, plot=True):
    scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge1_scores = []
    rouge2_scores = []
    rougeL_scores = []
    
    for i, (pred, ref) in enumerate(zip(predictions, references)):
        scores = scorer.score(ref, pred)
        rouge1_scores.append(scores['rouge1'].fmeasure)
        rouge2_scores.append(scores['rouge2'].fmeasure)
        rougeL_scores.append(scores['rougeL'].fmeasure)
    
    # Plot individual ROUGE scores if requested
    if plot and len(predictions) > 1:
        plt.figure(figsize=(12, 6))
        x = range(len(predictions))
        plt.plot(x, rouge1_scores, 'o-', label='ROUGE-1')
        plt.plot(x, rouge2_scores, 's-', label='ROUGE-2')
        plt.plot(x, rougeL_scores, '^-', label='ROUGE-L')
        plt.xlabel('Example Index')
        plt.ylabel('ROUGE Score')
        plt.title('Individual ROUGE Scores for Each Example')
        plt.legend()
        plt.grid(True, linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('individual_rouge_scores.png')
        plt.close()
        
        # Create a bar plot of average ROUGE scores
        plt.figure(figsize=(8, 5))
        avg_scores = [
            sum(rouge1_scores) / len(rouge1_scores),
            sum(rouge2_scores) / len(rouge2_scores),
            sum(rougeL_scores) / len(rougeL_scores)
        ]
        plt.bar(['ROUGE-1', 'ROUGE-2', 'ROUGE-L'], avg_scores, color=['blue', 'green', 'red'])
        plt.ylabel('Average Score')
        plt.title('Average ROUGE Scores')
        plt.grid(True, axis='y', linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('average_rouge_scores.png')
        plt.close()
    
    return {
        'rouge1': sum(rouge1_scores) / len(rouge1_scores) if rouge1_scores else 0,
        'rouge2': sum(rouge2_scores) / len(rouge2_scores) if rouge2_scores else 0,
        'rougeL': sum(rougeL_scores) / len(rougeL_scores) if rougeL_scores else 0,
        'individual_rouge1': rouge1_scores,
        'individual_rouge2': rouge2_scores,
        'individual_rougeL': rougeL_scores
    }

# 2. BLEU Score with individual plots
def calculate_bleu(predictions, references, plot=True):
    bleu_scores = []
    smoothing = SmoothingFunction().method1
    
    for pred, ref in zip(predictions, references):
        pred_tokens = word_tokenize(pred.lower())
        ref_tokens = [word_tokenize(ref.lower())]
        
        try:
            # Calculate BLEU score with smoothing for cases where n-gram precisions might be zero
            score = sentence_bleu(ref_tokens, pred_tokens, smoothing_function=smoothing)
            bleu_scores.append(score)
        except Exception as e:
            print(f"Error calculating BLEU: {e}")
            bleu_scores.append(0)
    
    # Plot individual BLEU scores if requested
    if plot and len(predictions) > 1:
        plt.figure(figsize=(10, 5))
        plt.bar(range(len(bleu_scores)), bleu_scores, color='skyblue')
        plt.xlabel('Example Index')
        plt.ylabel('BLEU Score')
        plt.title('Individual BLEU Scores for Each Example')
        plt.grid(True, axis='y', linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('individual_bleu_scores.png')
        plt.close()
    
    return {
        'average': sum(bleu_scores) / len(bleu_scores) if bleu_scores else 0,
        'individual': bleu_scores
    }

# 3. Word-level F1 Score with individual plots
def calculate_f1(predictions, references, plot=True):
    precision_scores = []
    recall_scores = []
    f1_scores = []
    
    for pred, ref in zip(predictions, references):
        # Tokenize and convert to lowercase
        pred_tokens = set(word_tokenize(pred.lower()))
        ref_tokens = set(word_tokenize(ref.lower()))
        
        # Calculate precision, recall, and F1
        if len(pred_tokens) == 0:
            precision = 0
        else:
            precision = len(pred_tokens.intersection(ref_tokens)) / len(pred_tokens)
        precision_scores.append(precision)
        
        if len(ref_tokens) == 0:
            recall = 0
        else:
            recall = len(pred_tokens.intersection(ref_tokens)) / len(ref_tokens)
        recall_scores.append(recall)
        
        if precision + recall == 0:
            f1 = 0
        else:
            f1 = 2 * precision * recall / (precision + recall)
        f1_scores.append(f1)
    
    # Plot individual F1, precision, and recall scores if requested
    if plot and len(predictions) > 1:
        plt.figure(figsize=(12, 6))
        x = range(len(predictions))
        plt.plot(x, precision_scores, 'o-', label='Precision')
        plt.plot(x, recall_scores, 's-', label='Recall')
        plt.plot(x, f1_scores, '^-', label='F1 Score')
        plt.xlabel('Example Index')
        plt.ylabel('Score')
        plt.title('Individual Precision, Recall, and F1 Scores')
        plt.legend()
        plt.grid(True, linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('individual_f1_scores.png')
        plt.close()
    
    return {
        'average_f1': sum(f1_scores) / len(f1_scores) if f1_scores else 0,
        'average_precision': sum(precision_scores) / len(precision_scores) if precision_scores else 0,
        'average_recall': sum(recall_scores) / len(recall_scores) if recall_scores else 0,
        'individual_f1': f1_scores,
        'individual_precision': precision_scores,
        'individual_recall': recall_scores
    }

# 4. Answer Relevancy (Semantic Similarity using Sentence-BERT)
def calculate_relevancy(predictions, references, model_name='all-MiniLM-L6-v2', plot=True):
    # Load the sentence transformer model
    model = SentenceTransformer(model_name)
    
    relevancy_scores = []
    
    for pred, ref in zip(predictions, references):
        # Get embeddings
        pred_embedding = model.encode(pred)
        ref_embedding = model.encode(ref)
        
        # Calculate cosine similarity
        similarity = np.dot(pred_embedding, ref_embedding) / (np.linalg.norm(pred_embedding) * np.linalg.norm(ref_embedding))
        relevancy_scores.append(similarity)
    
    # Plot individual relevancy scores if requested
    if plot and len(predictions) > 1:
        plt.figure(figsize=(10, 5))
        plt.bar(range(len(relevancy_scores)), relevancy_scores, color='lightgreen')
        plt.xlabel('Example Index')
        plt.ylabel('Semantic Similarity Score')
        plt.title('Answer Relevancy Scores for Each Example')
        plt.grid(True, axis='y', linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('individual_relevancy_scores.png')
        plt.close()
    
    return {
        'average': sum(relevancy_scores) / len(relevancy_scores) if relevancy_scores else 0,
        'individual': relevancy_scores
    }

def calculate_llm_relevancy(predictions, references, plot=True):
    llm_relevancy_scores = []
    
    for i, (pred, ref) in enumerate(zip(predictions, references)):
        try:
            # Create prompt for the LLM to evaluate similarity
            prompt = f"""
On a scale of 0 to 1, where 0 means completely different and 1 means semantically identical, 
provide a single number for how similar these two answers are in terms of content, meaning, and correctness.
Just return a decimal value between 0 and 1 without any explanation.

Generated Answer: {pred}
Reference Answer: {ref}

Similarity Score (0-1):
"""
            
            # Call Groq API with Whisper-large-v3-turbo
            response = groq_client.chat.completions.create(
                model="llama3-70b-8192",  # Assuming this model is available on Groq
                messages=[
                    {"role": "system", "content": "You are a scoring system that evaluates the semantic similarity between two answers."},
                    {"role": "user", "content": prompt}
                ],
                temperature=0.0,
                max_tokens=5
            )
            
            # Extract the score from the response
            score_text = response.choices[0].message.content.strip()
            # Parse the score, assuming it's a decimal between 0 and 1
            try:
                score = float(score_text)
                # Ensure score is between 0 and 1
                score = max(0, min(1, score))
            except ValueError:
                # If parsing fails, use a default or estimated score
                # Find a number in the response using regex
                score_match = re.search(r'(\d+(\.\d+)?)', score_text)
                if score_match:
                    score = float(score_match.group(1))
                    score = max(0, min(1, score))
                else:
                    print(f"Could not parse score from response: {score_text}")
                    score = 0.5  # Default mid-point score
            
            llm_relevancy_scores.append(score)
            
            # Optional: Print progress
            print(f"Processed example {i+1}/{len(predictions)}, LLM score: {score}")
            
        except Exception as e:
            print(f"Error with LLM-based evaluation for example {i}: {e}")
            # Assign a default mid-point score in case of errors
            llm_relevancy_scores.append(0.5)
    
    # Plot individual LLM relevancy scores if requested
    if plot and len(predictions) > 1:
        plt.figure(figsize=(10, 5))
        plt.bar(range(len(llm_relevancy_scores)), llm_relevancy_scores, color='purple')
        plt.xlabel('Example Index')
        plt.ylabel('LLM Relevancy Score')
        plt.title('LLM-based Answer Relevancy Scores')
        plt.grid(True, axis='y', linestyle='--', alpha=0.7)
        plt.tight_layout()
        plt.savefig('llm_relevancy_scores.png')
        plt.close()
        
        # Create a comparison plot between embedding-based and LLM-based relevancy
        if 'embedding_relevancy_scores' in globals():
            plt.figure(figsize=(12, 6))
            width = 0.35
            x = np.arange(len(llm_relevancy_scores))
            plt.bar(x - width/2, embedding_relevancy_scores, width, label='Embedding-based')
            plt.bar(x + width/2, llm_relevancy_scores, width, label='LLM-based')
            plt.xlabel('Example Index')
            plt.ylabel('Relevancy Score')
            plt.title('Comparison of Embedding-based vs LLM-based Relevancy')
            plt.legend()
            plt.grid(True, axis='y', linestyle='--', alpha=0.7)
            plt.tight_layout()
            plt.savefig('relevancy_comparison.png')
            plt.close()
    
    return {
        'average': sum(llm_relevancy_scores) / len(llm_relevancy_scores) if llm_relevancy_scores else 0,
        'individual': llm_relevancy_scores
    }
    
# Plot performance metrics: upsert and RAG times vs number of chunks
def plot_performance_metrics(upsert_times, rag_times, chunk_counts):
    # Create a figure with two subplots side by side
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 6))
    
    # Plot 1: Upsert Time vs Number of Chunks
    ax1.scatter(chunk_counts, upsert_times, color='blue', alpha=0.7)
    ax1.set_xlabel('Number of Chunks')
    ax1.set_ylabel('Upsert Time (seconds)')
    ax1.set_title('Document Upsert Time vs Number of Chunks')
    
    # Add trend line
    if len(chunk_counts) > 1:
        z = np.polyfit(chunk_counts, upsert_times, 1)
        p = np.poly1d(z)
        ax1.plot(chunk_counts, p(chunk_counts), "r--", alpha=0.7)
    
    ax1.grid(True, linestyle='--', alpha=0.7)
    
    # Plot 2: RAG Processing Time vs Number of Chunks
    ax2.scatter(chunk_counts, rag_times, color='green', alpha=0.7)
    ax2.set_xlabel('Number of Chunks')
    ax2.set_ylabel('RAG Processing Time (seconds)')
    ax2.set_title('RAG Processing Time vs Number of Chunks')
    
    # Add trend line
    if len(chunk_counts) > 1:
        z = np.polyfit(chunk_counts, rag_times, 1)
        p = np.poly1d(z)
        ax2.plot(chunk_counts, p(chunk_counts), "r--", alpha=0.7)
    
    ax2.grid(True, linestyle='--', alpha=0.7)
    
    plt.tight_layout()
    plt.savefig('performance_metrics.png')
    plt.close()
    
    # Create an additional plot showing both metrics together
    plt.figure(figsize=(10, 6))
    plt.scatter(chunk_counts, upsert_times, color='blue', label='Upsert Time', alpha=0.7)
    plt.scatter(chunk_counts, rag_times, color='green', label='RAG Time', alpha=0.7)
    
    # Add trend lines
    if len(chunk_counts) > 1:
        z1 = np.polyfit(chunk_counts, upsert_times, 1)
        p1 = np.poly1d(z1)
        plt.plot(chunk_counts, p1(chunk_counts), "b--", alpha=0.7)
        
        z2 = np.polyfit(chunk_counts, rag_times, 1)
        p2 = np.poly1d(z2)
        plt.plot(chunk_counts, p2(chunk_counts), "g--", alpha=0.7)
    
    plt.xlabel('Number of Chunks')
    plt.ylabel('Time (seconds)')
    plt.title('Upsert Time and RAG Time vs Number of Chunks')
    plt.legend()
    plt.grid(True, linestyle='--', alpha=0.7)
    plt.tight_layout()
    plt.savefig('combined_performance_metrics.png')
    plt.close()

# Run all evaluations and create plots
def evaluate_rag_pipeline(generated_answers, true_answers, upsert_times, rag_times, chunk_counts):
    # Calculate evaluation metrics with plots
    rouge_results = calculate_rouge(generated_answers, true_answers)
    bleu_results = calculate_bleu(generated_answers, true_answers)
    f1_results = calculate_f1(generated_answers, true_answers)
    relevancy_results = calculate_relevancy(generated_answers, true_answers)
    
    # Save the embedding-based relevancy scores for comparison
    global embedding_relevancy_scores
    embedding_relevancy_scores = relevancy_results['individual']
    
    # Calculate LLM-based relevancy
    llm_relevancy_results = calculate_llm_relevancy(generated_answers, true_answers)
    
    # Plot performance metrics
    if len(upsert_times) == len(rag_times) == len(chunk_counts) and len(upsert_times) > 1:
        plot_performance_metrics(upsert_times, rag_times, chunk_counts)
    
    # Compile results
    results = {
        'ROUGE': rouge_results,
        'BLEU': bleu_results,
        'F1 Score': f1_results,
        'Answer Relevancy': relevancy_results,
        'LLM Relevancy': llm_relevancy_results
    }
    
    return results

In [8]:
qa = pd.read_csv('/kaggle/input/check-it-out/legal_cases_with_docs_new.csv')
qa

case_name    judgment_date  \
0          Union of India vs. Maj. Gen. Manomoy Ganguly  1st August 2018   
1          Union of India vs. Maj. Gen. Manomoy Ganguly  1st August 2018   
2          Union of India vs. Maj. Gen. Manomoy Ganguly  1st August 2018   
3          Union of India vs. Maj. Gen. Manomoy Ganguly  1st August 2018   
4          Union of India vs. Maj. Gen. Manomoy Ganguly  1st August 2018   
...                                                 ...              ...   
1812  Glocal Medical College and Super Speciality Ho...              NaN   
1813  J.H. Patel (D) By LRS and Others vs. Nuboard M...              NaN   
1814  J.H. Patel (D) By LRS and Others vs. Nuboard M...              NaN   
1815  J.H. Patel (D) By LRS and Others vs. Nuboard M...              NaN   
1816  J.H. Patel (D) By LRS and Others vs. Nuboard M...              NaN   

                                               question  \
0     Who is the respondent in the case Union of Ind...   
1     What was the main issue in the case Union of I...   
2     What decision did the Armed Forces Tribunal (A...   
3     What was the reason given by the appellants fo...   
4     How did the Supreme Court of India rule on the...   
...                                                 ...   
1812  What was the Supreme Court's decision regardin...   
1813  What was the main issue in the case of J.H. Pa...   
1814  What were the circumstances that led to the di...   
1815  What was the Labour Court's decision regarding...   
1816  What did the High Court decide regarding the L...   

                                                 answer  \
0          The respondent is Maj. Gen. Manomoy Ganguly.   
1     The main issue was Maj. Gen. Manomoy Ganguly's...   
2     The AFT directed the appellants to post Maj. G...   
3     The appellants argued that Maj. Gen. Manomoy G...   
4     The Supreme Court of India upheld the AFT's de...   
...                                                 ...   
1812  The Supreme Court set aside the cancellation o...   
1813  The main issue was the challenge to the High C...   
1814  The workmen, including J.H. Patel, were dismis...   
1815  The Labour Court found that while the miscondu...   
1816  The High Court set aside the Labour Court's aw...   

                                                    doc  
0     Union Of India vs Maj Gen Manomoy Ganguly Vsm ...  
1     Union Of India vs Maj Gen Manomoy Ganguly Vsm ...  
2     Union Of India vs Maj Gen Manomoy Ganguly Vsm ...  
3     Union Of India vs Maj Gen Manomoy Ganguly Vsm ...  
4     Union Of India vs Maj Gen Manomoy Ganguly Vsm ...  
...                                                 ...  
1812  Modern Institute Of Medical Sciences ... vs Un...  
1813                     Error: Failed after 3 attempts  
1814                     Error: Failed after 3 attempts  
1815                     Error: Failed after 3 attempts  
1816                     Error: Failed after 3 attempts  

[1817 rows x 5 columns]

In [9]:
qa.iloc[100]['question']

'What is the significance of Section 8 and Section 12 of the Hindu Adoptions and Maintenance Act, 1956, in this case?'

In [10]:
generated_ans = []
queries = []
true_ans = list(qa.iloc[:200]['answer'])

In [11]:
# error_str =  "I don't have enough information to answer this question."

In [12]:
for i in range(200):
    ga = process_newdata_query(qa.iloc[i]['question'],qa.iloc[i]['doc'])
    generated_ans.append(ga['answer'])
    queries.append(ga['query'])

True  time  16.813607692718506
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.329066276550293
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.39600658416748
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.729910850524902
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.4502534866333
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.313968181610107
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.23709464073181
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True  time  16.28775405883789
Retrieving similar documents...
Type of retrieved_results: <class 'str'>
Generating answer...
True 

In [13]:
# Run evaluation with the sample data
evaluation_results = evaluate_rag_pipeline(generated_ans, true_ans, time_duration_upsert, time_duration_rag, num_chunks)

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processed example 1/200, LLM score: 0.95
Processed example 2/200, LLM score: 0.4
Processed example 3/200, LLM score: 0.2
Processed example 4/200, LLM score: 0
Processed example 5/200, LLM score: 0
Processed example 6/200, LLM score: 0
Processed example 7/200, LLM score: 0.2
Processed example 8/200, LLM score: 0.85
Processed example 9/200, LLM score: 0.98
Processed example 10/200, LLM score: 0
Processed example 11/200, LLM score: 0.1
Processed example 12/200, LLM score: 0.1
Processed example 13/200, LLM score: 0.7
Processed example 14/200, LLM score: 0.8
Processed example 15/200, LLM score: 0.7
Processed example 16/200, LLM score: 0.8
Processed example 17/200, LLM score: 0.7
Processed example 18/200, LLM score: 0.2
Processed example 19/200, LLM score: 0.83
Processed example 20/200, LLM score: 0.6
Processed example 21/200, LLM score: 0
Processed example 22/200, LLM score: 0
Processed example 23/200, LLM score: 0
Processed example 24/200, LLM score: 0.2
Processed example 25/200, LLM score

In [14]:
# Create a comprehensive dashboard of results
def create_results_dashboard(results, upsert_times, rag_times, chunk_counts):
    # Create a DataFrame for performance metrics
    if len(upsert_times) == len(rag_times) == len(chunk_counts):
        perf_df = pd.DataFrame({
            'Number of Chunks': chunk_counts,
            'Upsert Time (s)': upsert_times,
            'RAG Time (s)': rag_times
        })
        
        print("Performance Metrics Summary:")
        print(perf_df.describe())
        
        # Calculate correlation between chunk counts and processing times
        if len(chunk_counts) > 1:
            upsert_corr = np.corrcoef(chunk_counts, upsert_times)[0, 1]
            rag_corr = np.corrcoef(chunk_counts, rag_times)[0, 1]
            print(f"\nCorrelation between Chunks and Upsert Time: {upsert_corr:.4f}")
            print(f"Correlation between Chunks and RAG Time: {rag_corr:.4f}")
    
    # Print evaluation metrics
    print("\nRAG Pipeline Evaluation Results:")
    print(f"ROUGE-1: {results['ROUGE']['rouge1']:.4f}")
    print(f"ROUGE-2: {results['ROUGE']['rouge2']:.4f}")
    print(f"ROUGE-L: {results['ROUGE']['rougeL']:.4f}")
    print(f"BLEU Score: {results['BLEU']['average']:.4f}")
    print(f"F1 Score: {results['F1 Score']['average_f1']:.4f}")
    print(f"Precision: {results['F1 Score']['average_precision']:.4f}")
    print(f"Recall: {results['F1 Score']['average_recall']:.4f}")
    print(f"Embedding-based Relevancy: {results['Answer Relevancy']['average']:.4f}")
    print(f"LLM-based Relevancy: {results['LLM Relevancy']['average']:.4f}")
    
    # Calculate correlation between relevancy metrics
    embedding_scores = results['Answer Relevancy']['individual']
    llm_scores = results['LLM Relevancy']['individual']
    if len(embedding_scores) == len(llm_scores) and len(embedding_scores) > 1:
        relevancy_corr = np.corrcoef(embedding_scores, llm_scores)[0, 1]
        print(f"\nCorrelation between Embedding-based and LLM-based Relevancy: {relevancy_corr:.4f}")
    
    # Create a table comparing all metrics
    print("\nMetric Comparison Table:")
    metric_df = pd.DataFrame({
        'ROUGE-1': [results['ROUGE']['rouge1']],
        'ROUGE-2': [results['ROUGE']['rouge2']],
        'ROUGE-L': [results['ROUGE']['rougeL']],
        'BLEU': [results['BLEU']['average']],
        'F1': [results['F1 Score']['average_f1']],
        'Emb-Relevancy': [results['Answer Relevancy']['average']],
        'LLM-Relevancy': [results['LLM Relevancy']['average']]
    })
    print(metric_df.T)

In [15]:
create_results_dashboard(evaluation_results, time_duration_upsert, time_duration_rag, num_chunks)

Performance Metrics Summary:
       Number of Chunks  Upsert Time (s)  RAG Time (s)
count        200.000000       200.000000    200.000000
mean          15.485000        16.567792      1.115082
std           16.708851         0.820432      0.173460
min            1.000000        15.790723      0.967697
25%            4.000000        16.123888      1.024274
50%            9.000000        16.360472      1.059864
75%           19.000000        16.730733      1.157223
max           74.000000        25.089715      2.800595

Correlation between Chunks and Upsert Time: 0.6272
Correlation between Chunks and RAG Time: -0.0559

RAG Pipeline Evaluation Results:
ROUGE-1: 0.1486
ROUGE-2: 0.0646
ROUGE-L: 0.1204
BLEU Score: 0.0374
F1 Score: 0.1819
Precision: 0.2281
Recall: 0.1856
Embedding-based Relevancy: 0.2940
LLM-based Relevancy: 0.1748

Correlation between Embedding-based and LLM-based Relevancy: 0.8572

Metric Comparison Table:
                      0
ROUGE-1        0.148589
ROUGE-2        0.06

In [16]:
# Additional statistics about the RAG system performance
if time_duration_upsert and time_duration_rag and num_chunks:
    print("\nRAG System Performance Metrics:")
    print(f"Average Document Upsert Time: {sum(time_duration_upsert)/len(time_duration_upsert):.2f} seconds")
    print(f"Average RAG Processing Time: {sum(time_duration_rag)/len(time_duration_rag):.2f} seconds")
    print(f"Average Number of Chunks: {sum(num_chunks)/len(num_chunks):.2f}")


RAG System Performance Metrics:
Average Document Upsert Time: 16.57 seconds
Average RAG Processing Time: 1.12 seconds
Average Number of Chunks: 15.48


In [17]:
generated_ans

['The respondent in the case Union of India vs. Maj. Gen. Manomoy Ganguly is Maj. Gen. Manomoy Ganguly, VSM.',
 "The main issue in the case Union of India vs. Maj. Gen. Manomoy Ganguly was the non-empanelment of the respondent (Maj. Gen. Manomoy Ganguly) for promotion to the rank of Lieutenant General (Lt. Gen.) despite his outstanding academic and service record, and the subsequent quashing of the Review Special Promotion Board's proceedings by the Armed Forces Tribunal (AFT) due to the allotment of wrong board marks to the respondent.",
 'The Armed Forces Tribunal (AFT) quashed the proceedings of the Review SPB and directed to convene a fresh Review SPB to consider Maj. Gen. Manomoy Ganguly for promotion to the rank of Lt. Gen. in consonance with the parameters of relevant policies and his changed profile after allotting entitled board marks. Additionally, the AFT directed to restore his seniority.',
 "I don't have enough information to answer this question.",
 "I don't have enough i

In [18]:
import matplotlib.pyplot as plt


# NO Q/A dataset
Data Preprocessing to fillna and then combine all the columns

In [19]:
# # Load the CSV file and process its content
# csv_file_path = "/kaggle/input/legal-text-classification-dataset/legal_text_classification.csv"
# df = pd.read_csv(csv_file_path)
# # Handle missing values by filling them with empty strings
# df['case_title'] = df['case_title'].fillna("")
# df['case_outcome'] = df['case_outcome'].fillna("")
# df['case_text'] = df['case_text'].fillna("")

# # Combine columns into a single text for indexing
# df['content'] = (
#     "Case Title: " + df['case_title'] + "\n" +
#     "Case Outcome: " + df['case_outcome'] + "\n" +
#     "Case Text: " + df['case_text']
# )
# df

In [20]:
# content = list(df['content'])
# ids = list(df['case_id'])
# data = []
# for i in range(len(ids)):
#     data.append({'id':ids[i],'text':content[i]})

In [21]:

# data[0]['text']

Inputting/Upserting to Pincecone DB 

In [22]:
# import time
# for i in range(96,len(data)-96,96):
#     datas = data[i:i+96]
#     embeddings = pc.inference.embed(
#         model="multilingual-e5-large",
#         inputs=[d['text'] for d in datas],
#         parameters={"input_type": "passage", "truncate": "END"}
#     )
#     pinecone_index = pc.Index(index_name)
#     records = []
#     for d, e in zip(datas, embeddings):
#         records.append({
#             "id": d['id'],
#             "values": e['values'],
#             "metadata": {'text': d['text']}
#         })
    
#     # Upsert the records into the index
#     pinecone_index.upsert(
#         vectors=records,
#         namespace=f"ind_{i}"
#     )
#     time.sleep(60)

# HF dataset with summary

In [23]:
!pip install datasets

In [24]:
from datasets import load_dataset

# df = load_dataset("ninadn/indian-legal")
# df

In [25]:
# train = pd.DataFrame(df['train'])
# train_text = list(train['Text'])
# train_summary = list(train['Summary'])

In [26]:
# train_text[3]

In [27]:
# import nltk
# from nltk.tokenize import sent_tokenize, word_tokenize

# nltk.download("punkt_tab")  # Download NLTK tokenizer model

In [28]:
# def chunk_text(text, max_tokens=505):
#     """Splits text into chunks of max 505 tokens while keeping sentence structure intact."""
#     sentences = sent_tokenize(text)  # Split into sentences
#     chunks = []
#     current_chunk = []
#     current_length = 0

#     for sentence in sentences:
#         words = word_tokenize(sentence)  # Tokenize words
#         sentence_length = len(words)

#         if current_length + sentence_length > max_tokens:
#             if current_chunk:
#                 chunks.append(" ".join(current_chunk))  # Save previous chunk
#             current_chunk = words  # Start new chunk
#             current_length = sentence_length
#         else:
#             current_chunk.extend(words)
#             current_length += sentence_length

#     if current_chunk:
#         chunks.append(" ".join(current_chunk))  # Add last chunk

#     return chunks

In [29]:
df = pd.read_csv('/kaggle/input/legalsummary/HFsummarydataset.csv')
df

Unnamed: 0          id  \
0               0      ns_0_0   
1               1      ns_0_1   
2               2      ns_0_2   
3               3      ns_0_3   
4               4      ns_0_4   
...           ...         ...   
74015       74015  ns_7029_68   
74016       74016  ns_7029_69   
74017       74017  ns_7029_70   
74018       74018  ns_7029_71   
74019       74019  ns_7029_72   

                                                    text  \
0      Appeal No . LXVI of 1949 . Appeal from the Hig...   
1      The decision of the point depends firstly on t...   
2      The Privy Council held that the amount paid by...   
3      It is therefore clear that there is no conflic...   
4      Sections 143to 168 concern themselves with the...   
...                                                  ...   
74015  In effect and substance the said procedure has...   
74016  The following relevant rules may be extracted ...   
74017  Both are wide in scope , and it is doubtful wh...   
74018  ( 5 ) Subject to the overriding power of the c...   
74019  In a conflict between the administration of ju...   

                                                 summary  
0      The charge created in respect of municipal pro...  
1      The charge created in respect of municipal pro...  
2      The charge created in respect of municipal pro...  
3      The charge created in respect of municipal pro...  
4      The charge created in respect of municipal pro...  
...                                                  ...  
74015  The respondent who was a District and Sessions...  
74016  The respondent who was a District and Sessions...  
74017  The respondent who was a District and Sessions...  
74018  The respondent who was a District and Sessions...  
74019  The respondent who was a District and Sessions...  

[74020 rows x 4 columns]

In [30]:
data = []
chunks_text = list(df['text'])
summary_text = list(df['summary'])
ids = list(df['id'])


In [31]:
for i in range(len(ids)):    
    data.append({'id':ids[i],'text':chunks_text[i],'summary':summary_text[i]})

In [32]:
# data = []
# for i in range(len(train_text)):
#     chunks = chunk_text(train_text[i])
#     for j in range(len(chunks)):
#         data.append({'id':'ns_'+str(i)+'_'+str(j),'text':chunks[j],'summary':train_summary[i]})

In [33]:
data[0]['summary']

'The charge created in respect of municipal property tax by section 212 of the City of Bombay Municipal Act, 1888, is an "annual charge not being a capital charge" within the mean ing of section 9 (1) (iv) of the Indian Income tax Act, 199.2, and the amount of such charge should therefore be deducted in computing the income from such property for the purposes of section 9 of the Indian Income tax Act.\nThe charge in respect of urban immoveable property tax created by the Bombay Finance Act, 1939 is similar in character and the amount of such charge should also be deducted.\nThe expression "capital charge" in s.9(1) (iv) means a charge created for a capital sum,that is to say, a charge created to. \' secure the discharge of a liability of a capi tal nature; and an "annual charge" means a charge to secure an annual liabili ty. 554\n'

# upsert HF dataset to Pinecone

In [34]:
# import time

# # Define a function to truncate text to fit metadata limits
# def truncate_text(text, max_bytes=40960):
#     """Truncate text to ensure metadata size doesn't exceed the limit."""
#     while len(text.encode('utf-8')) > max_bytes:
#         text = text[:-100]  # Remove 100 characters at a time
#     return text
# namespace_count=35
# # Process data in batches
# for i in range(61824, len(data) - 192, 192):
#     if i%1920==0:
#         namespace_count+=1
#     try:
#         datas = []
#         embeddings = []
#         for j in range(1,3):
#             # Slice the data batch
#             s = i+(j-1)*96
#             e = i+j*96
#             datas.append(data[s:e])
#             # Generate embeddings
#             emb = pc_duplicate.inference.embed(
#                 model="multilingual-e5-large",
#                 inputs=[d['text'] for d in datas[j-1]],
#                 parameters={"input_type": "passage", "truncate": "END"}
#             )
#             embeddings.append(emb) 
#             time.sleep(15)
#         # Prepare records for Pinecone
#         records = []
#         for j in range(len(datas)):
#             for d, e in zip(datas[j], embeddings[j]):
#                 try:
#                     # # Truncate text if metadata exceeds the limit
#                     truncated_text = d['text']
#                     summary_text = d['summary']
                    
#                     # Add the record
#                     records.append({
#                         "id": d['id'],
#                         "values": e['values'],
#                         "metadata": {"text": truncated_text,'summary':summary_text}
#                     })
#                 except Exception as inner_error:
#                     print(f"Error processing record ID {d['id']}: {inner_error}")
            
#         # Upsert records into the Pinecone index
#         pinecone_index = pc.Index(index_name)
#         pinecone_index.upsert(
#             vectors=records,
#             namespace=f"ind_{namespace_count}"
#         )
#     except Exception as batch_error:
#         print(f"Error processing batch {i}: {batch_error}")


In [35]:
# # Create a Pinecone index
# q_index_name = "legaltextcasequery"
# if index_name not in pc_duplicate.list_indexes().names():
#     pc_duplicate.create_index(
#         name=q_index_name, 
#         dimension=1024, 
#         metric='cosine',
#         spec=ServerlessSpec(
#             cloud='aws',
#             region='us-east-1'
#         )
#     )

In [36]:
# # Define your query
# query = "What is the section that sets up machinery to assess tax liabilities of firms which have discontinued their business?"

# # Convert the query into a numerical vector that Pinecone can search with
# query_embedding = pc_duplicate.inference.embed(
#     model="multilingual-e5-large",
#     inputs=[query],
#     parameters={
#         "input_type": "query"
#     }
# )

In [37]:
# q_records = []
# q_results = pc_duplicate.Index(q_index_name).query(
#     namespace="q_ind",
#     vector=query_embedding[0].values,
#     top_k=3,
#     include_values=False,
#     include_metadata=True 
# )
# if q_results['matches']:
#     print('Not empty')
# else:
#     print('empty')
    
    

In [38]:
# # Search the index for the three most similar vectors
# results = pc.Index(index_name).query(
#     namespace="ind_1",
#     vector=query_embedding[0].values,
#     top_k=3,
#     include_values=False,
#     include_metadata=True
# )

# print(results)

In [39]:
# def isSimilarQuery(query):
#     # Create a Pinecone index
#     q_index_name = "legaltextcasequery"
#     if q_index_name not in query_pc.list_indexes().names():
#         pc_duplicate.create_index(
#             name=q_index_name, 
#             dimension=1024, 
#             metric='cosine',
#             spec=ServerlessSpec(
#                 cloud='aws',
#                 region='us-east-1'
#             )
#         )
#     # Convert the query into a numerical vector that Pinecone can search with
#     query_embedding = pc_duplicate.inference.embed(
#         model="multilingual-e5-large",
#         inputs=[query],
#         parameters={
#             "input_type": "query"
#         }
#     )
#     q_results = query_pc.Index(q_index_name).query(
#         namespace="q_ind",
#         vector=query_embedding[0].values,
#         top_k=3,
#         include_values=False,
#         include_metadata=True 
#     )
#     q_records=[]
#     if q_results['matches'] and q_results['matches'][0]['score']>=0.8:
#         print('Query Present')
#         return q_results
#     else:
#         # Search the index for the three most similar vectors
#         results = pc.Index(index_name).query(
#             namespace="ind_1",
#             vector=query_embedding[0].values,
#             top_k=3,
#             include_values=False,
#             include_metadata=True
#         )
#         q_results= results
#         for i in range(3):
#             q_results['matches'][i]['metadata']['query'] = query
#             q_records.append({
#                 "id":q_results['matches'][i]['id'],
#                 "values":query_embedding[0].values,
#                 "metadata":q_results['matches'][i]['metadata'],
#             })
#         query_pc.Index(q_index_name).upsert(
#             vectors=q_records,
#             namespace="q_ind",
#         )
#         print('Query Upserted')
#         return q_records
    

In [40]:
# query = "What is the section that sets up machinery to assess tax liabilities of firms which have discontinued their business?"
# print(isSimilarQuery(query))

In [41]:
!pip install groq

In [42]:
# from groq import Groq

# # Set up Groq client
# groq_client = Groq(api_key="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")

# def generate_answer(query, retrieved_contexts):
#     # Extract the text content from retrieved documents
#     contexts = []
    
#     # Convert the Pinecone object to a dict for easier handling
#     if not isinstance(retrieved_contexts, dict):
#         retrieved_dict = retrieved_contexts.to_dict() if hasattr(retrieved_contexts, 'to_dict') else vars(retrieved_contexts)
#     else:
#         retrieved_dict = retrieved_contexts
    
#     # Extract text from matches
#     if 'matches' in retrieved_dict:
#         for match in retrieved_dict['matches']:
#             if 'metadata' in match and 'text' in match['metadata']:
#                 # In a real scenario this would contain the actual text
#                 text = match['metadata']['text']
#                 if text:  # Only add non-empty text
#                     contexts.append(text)
    
#     context_text = "\n\n".join(contexts)
#     prompt = f"""
# You are a helpful assistant specialized in Indian tax law. Use ONLY the following context to answer the question. 
# If you don't have enough information to answer this question, say "I don't have enough information to answer this question."

# Context:
# {context_text}

# Question: {query}

# Answer:
# """
    
#     # Generate answer using Groq's LLama model
#     try:
#         response = groq_client.chat.completions.create(
#             model="llama3-70b-8192",
#             messages=[
#                 {"role": "system", "content": "You are a helpful assistant that answers questions based only on the provided context."},
#                 {"role": "user", "content": prompt}
#             ],
#             temperature=0.2,
#             max_tokens=1024
#         )
#         return response.choices[0].message.content
#     except Exception as e:
#         return f"Error generating response: {str(e)}"

# def process_query(query):
#     # Add debugging information
#     print("Retrieving similar documents...")
#     retrieved_results = isSimilarQuery(query)
#     print(f"Type of retrieved_results: {type(retrieved_results)}")
    
#     print("Generating answer...")
#     answer = generate_answer(query, retrieved_results)
    
#     return {
#         "query": query,
#         "retrieved_contexts": retrieved_results,
#         "answer": answer
#     }

# # Example usage
# query = "What is the section that sets up machinery to assess tax liabilities of firms which have discontinued their business?"
# response = process_query(query)
# print("\nQuery:", query)
# print("\nGenerated Answer:", response["answer"])